In [16]:
from scholarly import scholarly
from docx import Document
from docx.shared import Pt, RGBColor
from docx.oxml.ns import qn

# Google Scholar User ID
USER_ID = "mbTEhB4AAAAJ"
KEYWORDS = ["Ken Shiozaki", "K. Shiozaki"]

# Scholarから情報取得
author = scholarly.search_author_id(USER_ID)
author_filled = scholarly.fill(author, sections=["publications"])

# 論文データ取得と整形
publications = []
for pub in author_filled["publications"]:
    pub_filled = scholarly.fill(pub)
    bib = pub_filled.get("bib", {})
    authors = bib.get("author", "")
    title = bib.get("title", "")
    journal = bib.get("journal", "")
    volume = bib.get("volume", "")
    pages = bib.get("pages", "")
    year = bib.get("pub_year", "")
    eprint = bib.get("eprint", "")
    citations = pub_filled.get("num_citations", 0)
    is_arxiv = "arxiv" in journal.lower() or "arxiv" in eprint.lower()
    publications.append({
        "authors": authors,
        "title": title,
        "journal": journal,
        "volume": volume,
        "pages": pages,
        "year": year,
        "arxiv": eprint,
        "citations": citations,
        "is_arxiv": is_arxiv,
    })

# 年順にソート（新→旧）
publications.sort(key=lambda x: x["year"] or "0000", reverse=True)

# Word文書初期化
doc = Document()
style = doc.styles['Normal']
style.font.name = 'Times New Roman'
style.font.size = Pt(11)

def set_font(run, bold=False):
    run.font.name = 'Times New Roman'
    run.font.size = Pt(11)
    run.bold = bold
    run._element.rPr.rFonts.set(qn('w:eastAsia'), 'Times New Roman')

def add_section(doc, entries, heading):
    doc.add_heading(heading, level=2)
    for entry in entries:
        para = doc.add_paragraph(style='List Number')  # Word段落番号付きリスト

        # 著者
        authors = entry["authors"].replace(" and ", ", ").split(", ")
        for j, name in enumerate(authors):
            if j > 0:
                run = para.add_run(", ")
                set_font(run)
            run = para.add_run(name)
            if name.strip() in KEYWORDS:
                run.font.underline = True
            set_font(run)

        # タイトル
        run = para.add_run(f', "{entry["title"]}", ')
        set_font(run)

        # 雑誌 + volume（太字） + page + year
        journal_text = entry["journal"]
        if journal_text:
            run = para.add_run(journal_text + " ")
            set_font(run)
        if entry["volume"]:
            run = para.add_run(entry["volume"])
            set_font(run, bold=True)
        if entry["pages"]:
            run = para.add_run(f", {entry['pages']}")
            set_font(run)
        if entry["year"]:
            run = para.add_run(f" ({entry['year']})")
            set_font(run)

        # arXiv
        if entry["arxiv"]:
            run = para.add_run(f"; {entry['arxiv']}")
            set_font(run)

        # 引用数（100件以上は赤字）
        citation_str = f". [Cited by {entry['citations']}]"
        run = para.add_run(citation_str)
        set_font(run)
        if entry["citations"] >= 100:
            run.font.color.rgb = RGBColor(255, 0, 0)  # 赤字

# 査読論文・arXiv に分割
journal_pubs = [p for p in publications if not p["is_arxiv"]]
arxiv_pubs = [p for p in publications if p["is_arxiv"]]

# セクションに出力
add_section(doc, journal_pubs, "I. 論文（査読有）")
add_section(doc, arxiv_pubs, "II. arXiv プレプリント")

# 保存
output_path = "Publications.docx"
doc.save(output_path)
print(f"保存完了: {output_path}")


保存完了: Publications.docx
